# Exploratory Data Analysis

Use this notebook to get familiar with the datasets we have. There is 10 questions we need to answer during the EDA.


We shouldn't limit our EDA to these 10 questions. Let's be creative :).

In [5]:
import pandas as pd
import numpy as np
import scipy.stats as st
import plotly.express as px

In [7]:
flights = pd.read_csv('C:/Users/danfv/OneDrive/Knowledge/Courses/Data Analysis/LHL - Data Analysis Bootcamp/lighthouse-data-notes/W6 Midterm Project/Midterm_Project/Data/Flights - Sample 50000 rand.csv').sort_values('fl_date').reset_index(drop=True)
flights = flights.drop('no_name', axis=1)
flights['total_delay'] = flights['carrier_delay'] + flights['weather_delay'] + flights['nas_delay'] + flights['security_delay'] + flights['late_aircraft_delay']
flights = flights.fillna(value={'total_delay' : 0})
flights.head()

fl_date mkt_unique_carrier branded_code_share mkt_carrier  \
0  2018-01-01                 DL                 DL          DL   
1  2018-01-01                 UA                 UA          UA   
2  2018-01-01                 WN                 WN          WN   
3  2018-01-01                 NK                 NK          NK   
4  2018-01-01                 NK                 NK          NK   

   mkt_carrier_fl_num op_unique_carrier tail_num  op_carrier_fl_num  \
0                 260                DL   N964DN                260   
1                2117                UA   N12109               2117   
2                1508                WN   N8306H               1508   
3                 967                NK   N639NK                967   
4                 467                NK   N525NK                467   

   origin_airport_id origin  ... distance  carrier_delay weather_delay  \
0              14869    SLC  ...      991            NaN           NaN   
1              12892    LAX  ...     2454            NaN           NaN   
2              13232    MDW  ...      584            NaN           NaN   
3              11042    CLE  ...     1025            0.0           0.0   
4              10721    BOS  ...     1368            NaN           NaN   

  nas_delay  security_delay  late_aircraft_delay  first_dep_time  \
0       NaN             NaN                  NaN             NaN   
1       NaN             NaN                  NaN             NaN   
2       NaN             NaN                  NaN             NaN   
3      24.0             0.0                  0.0             NaN   
4       NaN             NaN                  NaN             NaN   

   total_add_gtime  longest_add_gtime  total_delay  
0              NaN                NaN          0.0  
1              NaN                NaN          0.0  
2              NaN                NaN          0.0  
3              NaN                NaN         24.0  
4              NaN                NaN          0.0  

[5 rows x 42 columns]

# **Task 1**: Test the hypothesis that the delay is from Normal distribution. and that **mean** of the delay is 0. Be careful about the outliers.

### The visual way

In [9]:
# Visual Normality Check
fig = px.histogram(flights[flights.total_delay > 0], x="total_delay")
fig.show()
# not normal, BUT how to know which?

### The Quantile-Quantile Plot way:

In [1]:

from statsmodels.graphics.gofplots import qqplot

qqplot(flights['total_delay'].sample(5000), line='s').show()


NameError: name 'flights' is not defined

### The Shapiro Way:

In [ ]:
# test removing the null values
st.shapiro(flights['total_delay'][flights['total_delay'].isnull() == False].sample(5000))

# test replacing null with 0s
flights1 = flights.fillna(value={'total_delay' : 0})
st.shapiro(flights1['total_delay'].sample(5000))


# flights['total_delay'][flights['total_delay'].isnull() == False]


ShapiroResult(statistic=0.5255206227302551, pvalue=0.0)

### The normal test way:

In [ ]:
# test removing the null values
st.normaltest(flights['total_delay'][flights['total_delay'].isnull() == False].sample(5000))

# test replacing null with 0s
st.normaltest(flights1['total_delay'].sample(5000))

NormaltestResult(statistic=7299.069840054515, pvalue=0.0)

### Mean of the delay is 0: T-test doesn't work with non-normal distributes datasets

# **Task 2**: Is average/median monthly delay different during the year? If yes, which are months with the biggest delays and what could be the reason?

In [ ]:
delays = flights1.copy()[['fl_date', 'total_delay']]
delays['month'] = pd.DatetimeIndex(delays['fl_date']).month

In [ ]:
delays.groupby('month').mean()
# df.groupby('A').agg({'C': np.sum, 'D': np.max}) # agg lets me specify what do I want to do with each of the rest of the columns

total_delay
month             
1        12.915565
2        14.417228
3        10.659829
4        11.932116
5        13.979577
6        17.302375
7        15.834860
8        15.024761
9         9.762233
10       11.245875
11       11.262626
12       13.001692

#### **Task 3**: Does the weather affect the delay? 
Use the API to pull the weather information for flights. There is no need to get weather for ALL flights. We can choose the right representative sample. Let's focus on four weather types:
- sunny
- cloudy
- rainy
- snow.
Test the hypothesis that these 4 delays are from the same distribution. If they are not, which ones are significantly different?

In [ ]:
flights.columns

Index(['fl_date', 'mkt_unique_carrier', 'branded_code_share', 'mkt_carrier',
       'mkt_carrier_fl_num', 'op_unique_carrier', 'tail_num',
       'op_carrier_fl_num', 'origin_airport_id', 'origin', 'origin_city_name',
       'dest_airport_id', 'dest', 'dest_city_name', 'crs_dep_time', 'dep_time',
       'dep_delay', 'taxi_out', 'wheels_off', 'wheels_on', 'taxi_in',
       'crs_arr_time', 'arr_time', 'arr_delay', 'cancelled',
       'cancellation_code', 'diverted', 'dup', 'crs_elapsed_time',
       'actual_elapsed_time', 'air_time', 'flights', 'distance',
       'carrier_delay', 'weather_delay', 'nas_delay', 'security_delay',
       'late_aircraft_delay', 'first_dep_time', 'total_add_gtime',
       'longest_add_gtime', 'total_delay'],
      dtype='object')

# **Task 4**: How taxi times changing during the day? Does higher traffic lead to bigger taxi times?

In [219]:
taxi_times = flights.copy()[['fl_date', 'dep_time', 'arr_time', 'taxi_in', 'taxi_out']]

taxi_leaving = taxi_times[['dep_time', 'taxi_out']]
taxi_leaving = taxi_leaving.rename(columns={'dep_time' : 'time', 'taxi_out' : 'taxi'})
taxi_leaving['direction'] = 'outgoing'
taxi_arriving = taxi_times[['arr_time', 'taxi_in']]
taxi_arriving = taxi_arriving.rename(columns={'arr_time' : 'time', 'taxi_in' : 'taxi'})
taxi_arriving['direction'] = 'incoming'


taxi_total = taxi_leaving.append(taxi_arriving, ignore_index=True)
taxi_total

time  taxi direction
0      1717.0  26.0  outgoing
1      1150.0  18.0  outgoing
2      1344.0  15.0  outgoing
3      1520.0  42.0  outgoing
4      1414.0  16.0  outgoing
...       ...   ...       ...
99995  2214.0   3.0  incoming
99996   705.0  11.0  incoming
99997  1554.0   2.0  incoming
99998  1149.0   3.0  incoming
99999  1230.0   5.0  incoming

[100000 rows x 3 columns]

In [220]:
px.scatter(x = taxi_total.time, y = taxi_total.taxi, color=taxi_total.direction)

In [265]:
# generating the index for the training DF
taxi_ind_df = taxi_total.drop('direction', axis=1)
taxi_ind_df['time'] = (taxi_ind_df['time'] / 100).apply(np.floor)
taxi_ind_df = taxi_ind_df.groupby('time').sum()
taxi_ind_df['taxi_time_%'] = taxi_ind_df.taxi / taxi_ind_df.taxi.sum()
taxi_ind_df.drop('taxi', axis=1)['taxi_time_%'].to_dict()

{0.0: 0.008156744910698958,
 1.0: 0.0027025262535151783,
 2.0: 0.0008600046264541292,
 3.0: 0.0002788768516899051,
 4.0: 0.0023148390695185185,
 5.0: 0.02774663473822249,
 6.0: 0.048601142427888974,
 7.0: 0.05530305289552354,
 8.0: 0.06609300784804596,
 9.0: 0.0623523504240782,
 10.0: 0.05951360975456419,
 11.0: 0.05816597363888349,
 12.0: 0.057866140723193765,
 13.0: 0.05404407705061131,
 14.0: 0.05552470357244471,
 15.0: 0.059419307466565,
 16.0: 0.056478204484436495,
 17.0: 0.06176477462962172,
 18.0: 0.05965869019763986,
 19.0: 0.056196103622900465,
 20.0: 0.0532356565816952,
 21.0: 0.04302602340147547,
 22.0: 0.03243353905202827,
 23.0: 0.01814795142384365,
 24.0: 0.00011606435446053852}

# **Task 5**: What is the average percentage of delays that is already created before departure? (aka are arrival delays caused by departure delays?) Are airlines able to lower the delay during the flights?

In [ ]:
pd.set_option('display.max_columns', None)

# pd.reset_option('max_columns')

## Flow of a single airplane

In [ ]:
rand_airplane = pd.read_csv('C:/Users/danfv/OneDrive/Knowledge/Courses/Data Analysis/LHL - Data Analysis Bootcamp/lighthouse-data-notes/W6 Midterm Project/Midterm_Project/Data/Flights - Single random airplane.csv').sort_values('fl_date')
rand_airplane = rand_airplane.drop('no_name', axis=1)
rand_airplane['total_delay'] = rand_airplane['carrier_delay'] + rand_airplane['weather_delay'] + rand_airplane['nas_delay'] + rand_airplane['security_delay'] + rand_airplane['late_aircraft_delay']
rand_airplane#[rand_airplane.mkt_carrier_fl_num == 2117]

fl_date mkt_unique_carrier branded_code_share mkt_carrier  \
0     2018-01-01                 UA                 UA          UA   
1     2018-01-02                 UA                 UA          UA   
2     2018-01-02                 UA                 UA          UA   
3     2018-01-03                 UA                 UA          UA   
4     2018-01-03                 UA                 UA          UA   
...          ...                ...                ...         ...   
1162  2019-12-30                 UA                 UA          UA   
1163  2019-12-30                 UA                 UA          UA   
1165  2019-12-31                 UA                 UA          UA   
1164  2019-12-31                 UA                 UA          UA   
1166  2019-12-31                 UA                 UA          UA   

      mkt_carrier_fl_num op_unique_carrier tail_num  op_carrier_fl_num  \
0                   2117                UA   N12109               2117   
1                   2124                UA   N12109               2124   
2                   1784                UA   N12109               1784   
3                    665                UA   N12109                665   
4                    749                UA   N12109                749   
...                  ...               ...      ...                ...   
1162                 756                UA   N12109                756   
1163                 247                UA   N12109                247   
1165                1796                UA   N12109               1796   
1164                1111                UA   N12109               1111   
1166                1152                UA   N12109               1152   

      origin_airport_id origin   origin_city_name  dest_airport_id dest  \
0                 12892    LAX    Los Angeles, CA            11618  EWR   
1                 13204    MCO        Orlando, FL            11618  EWR   
2                 11618    EWR         Newark, NJ            13204  MCO   
3                 11618    EWR         Newark, NJ            12889  LAS   
4                 11292    DEN         Denver, CO            11618  EWR   
...                 ...    ...                ...              ...  ...   
1162              11618    EWR         Newark, NJ            14771  SFO   
1163              12892    LAX    Los Angeles, CA            11618  EWR   
1165              14771    SFO  San Francisco, CA            11618  EWR   
1164              14771    SFO  San Francisco, CA            12982  LIH   
1166              12982    LIH          Lihue, HI            14771  SFO   

         dest_city_name  crs_dep_time  dep_time  dep_delay  taxi_out  \
0            Newark, NJ          1200      1150        -10      18.0   
1            Newark, NJ          1003      1002         -1      27.0   
2           Orlando, FL           605       602         -3      16.0   
3         Las Vegas, NV          1930      1927         -3      24.0   
4            Newark, NJ          1245      1241         -4      19.0   
...                 ...           ...       ...        ...       ...   
1162  San Francisco, CA          2200      2342        102      20.0   
1163         Newark, NJ           715       730         15      13.0   
1165         Newark, NJ          2330      2334          4      23.0   
1164          Lihue, HI           905       925         20      15.0   
1166  San Francisco, CA          1425      1425          0      13.0   

      wheels_off  wheels_on  taxi_in  crs_arr_time  arr_time  arr_delay  \
0         1208.0     1944.0      7.0          2020    1951.0      -29.0   
1         1029.0     1233.0      7.0          1240    1240.0        0.0   
2          618.0      841.0     11.0           903     852.0      -11.0   
3         1951.0     2152.0      7.0          2221    2159.0      -22.0   
4         1300.0     1811.0      9.0          1829    1820.0       -9.0   
...          ...        ...      ...           ...       ...   

In [ ]:
flights[['dep_delay', 'arr_delay']].sum()
# flights[['dep_delay', 'arr_delay']].sum().dep_delay / flights[['dep_delay', 'arr_delay']].sum().arr_delay
dep_arr_delay = flights.copy()[['dep_delay', 'arr_delay']]
dep_arr_delay['decreased_delay'] = dep_arr_delay.dep_delay - dep_arr_delay.arr_delay


# % of flights that have a departure delay:
print("% of flights that have a departure delay:",
    dep_arr_delay.dep_delay[dep_arr_delay.dep_delay > 0].count() / dep_arr_delay.shape[0], sep='\n')

# % of flights that reduce the delay during the flight: 70%
print("% of flights that reduce the delay during the flight:",
        dep_arr_delay.decreased_delay[dep_arr_delay['decreased_delay'] > 0].count() / dep_arr_delay.shape[0], sep='\n')

dep_arr_delay

% of flights that have a departure delay:
0.34116
% of flights that reduce the delay during the flight:
0.69892


dep_delay  arr_delay  decreased_delay
27163        2.0       -1.0              3.0
7553       -10.0      -29.0             19.0
39374        9.0       -2.0             11.0
27211        0.0       24.0            -24.0
39196       -6.0       13.0            -19.0
...          ...        ...              ...
19861       -1.0       -5.0              4.0
22602       -5.0      -33.0             28.0
8196        -2.0      -30.0             28.0
4016         1.0      -11.0             12.0
45248       -5.0       -4.0             -1.0

[50000 rows x 3 columns]

# **Task 6**: How many states cover 50% of US air traffic? 

In [ ]:
states = flights.dest_city_name.str[-2:].value_counts().to_frame()
states['cum'] = states.dest_city_name.cumsum()
states = states.sort_values('dest_city_name', ascending=False)
states[states['cum'] <= 25000]
# states.sum()

dest_city_name    cum
CA            5473   5473
TX            4870  10343
FL            3523  13866
IL            3021  16887
GA            2732  19619
NY            2582  22201
NC            2374  24575

# **Task 7**: Test the hypothesis whether planes fly faster when there is the departure delay? 

In [ ]:
air_time = flights[['dep_delay', 'air_time']]
air_time
dep_arr_delay

dep_delay  arr_delay  decreased_delay
27163        2.0       -1.0              3.0
7553       -10.0      -29.0             19.0
39374        9.0       -2.0             11.0
27211        0.0       24.0            -24.0
39196       -6.0       13.0            -19.0
...          ...        ...              ...
19861       -1.0       -5.0              4.0
22602       -5.0      -33.0             28.0
8196        -2.0      -30.0             28.0
4016         1.0      -11.0             12.0
45248       -5.0       -4.0             -1.0

[50000 rows x 3 columns]

In [ ]:
dep_arr_delay[dep_arr_delay.dep_delay > 0]['decreased_delay'].mean()

4.662385861561119

In [ ]:
dep_arr_delay[dep_arr_delay.dep_delay <= 0]['decreased_delay'].mean()

5.268582291893914

# **Task 8**: When (which hour) do most 'LONG', 'SHORT', 'MEDIUM' haul flights take off?

In [ ]:
#create specific dataframe
haul = flights.copy()[['dep_time', 'air_time']]

#define haul category function
def haul_cat(minutes):
    if minutes < 180:
        return 'Short'
    elif minutes < 360:
        return 'Medium'
    else:
        return 'Long'

haul['haul_categ'] = haul.air_time.apply(lambda x: haul_cat(x))
haul

dep_time  air_time haul_categ
27163    1717.0     130.0      Short
7553     1150.0     276.0     Medium
39374    1344.0      79.0      Short
27211    1520.0     142.0      Short
39196    1414.0     217.0     Medium
...         ...       ...        ...
19861    2039.0      69.0      Short
22602     535.0      69.0      Short
8196     1437.0      66.0      Short
4016      926.0      66.0      Short
45248     940.0      66.0      Short

[50000 rows x 3 columns]

In [275]:
px.scatter(x=haul.dep_time, y=haul.air_time, color=haul.haul_categ).show()

## Airtime vs delays:

In [305]:
airtime_delay = flights.copy()[['air_time', 'total_delay']]
airtime_delay['airtime_bins'] = pd.cut(airtime_delay.air_time, bins=13, labels=range(13))
# airtime_delay = airtime_delay.drop('air_time', axis=1)
# airtime_delay = airtime_delay.groupby('airtime_bins').sum()
# airtime_delay['delays_for_airtime_%'] = airtime_delay.total_delay / airtime_delay.total_delay.sum()
airtime_delay

air_time  total_delay airtime_bins
0         130.0          0.0            2
1         276.0          0.0            5
2          79.0          0.0            1
3         142.0         24.0            2
4         217.0          0.0            4
...         ...          ...          ...
49995      69.0          0.0            1
49996      69.0          0.0            1
49997      66.0          0.0            1
49998      66.0          0.0            1
49999      66.0          0.0            1

[50000 rows x 3 columns]

In [300]:
px.bar(x=airtime_delay.index, y=airtime_delay['delays_for_airtime_%']).show()

In [302]:
airtime_delay.drop('total_delay', axis=1)['delays_for_airtime_%'].to_dict()

{0: 0.21342394833847084,
 1: 0.35026571661163297,
 2: 0.22531183208783437,
 3: 0.10185498550220896,
 4: 0.047492080333921785,
 5: 0.028251636527725693,
 6: 0.024073040816388756,
 7: 0.008076687369085404,
 8: 0.0009939600159765353,
 9: 0.00010061558443934253,
 10: 7.165049194922877e-05,
 11: 3.506300669855876e-05,
 12: 4.878331366756001e-05}

# **Task 9**: Find the top 10 the bussiest airports. Does the biggest number of flights mean that the biggest number of passengers went through the particular airport? How much traffic do these 10 airports cover?

In [ ]:
# top 10 airports by # of flights
airports = flights.copy()[['origin', 'origin_airport_id']]
airports_top10 = airports.groupby('origin').count().sort_values('origin_airport_id', ascending=False).head(10).reset_index()
airports_top10

origin  origin_airport_id
0    ORD               2488
1    ATL               2452
2    DFW               1799
3    DEN               1720
4    CLT               1609
5    LAX               1569
6    SEA               1200
7    DTW               1117
8    IAH               1116
9    PHX               1110

In [ ]:
# top 10 airports by number of passengers
passengers_top10_airp = pd.read_csv('C:/Users/danfv/OneDrive/Knowledge/Courses/Data Analysis/LHL - Data Analysis Bootcamp/lighthouse-data-notes/W6 Midterm Project/Midterm_Project/Data/Passengers - Top 10 Aiports Count.csv')
passengers_top10_airp

origin  count
0    ATL  65253
1    CLT  35573
2    DEN  57153
3    DFW  43244
4    DTW  43928
5    IAH  46173
6    LAX  52241
7    ORD  78217
8    PHX  30805
9    SEA  32069

In [ ]:
# top 10 airports by number of flights AND passengers
top10_flights_passen = pd.merge(airports_top10, passengers_top10_airp, on='origin', how='outer')
top10_flights_passen = top10_flights_passen.rename(columns={'origin_airport_id' : 'flights', 'count' : 'passengers'})
top10_flights_passen

origin  flights  passengers
0    ORD     2488       78217
1    ATL     2452       65253
2    DFW     1799       43244
3    DEN     1720       57153
4    CLT     1609       35573
5    LAX     1569       52241
6    SEA     1200       32069
7    DTW     1117       43928
8    IAH     1116       46173
9    PHX     1110       30805

In [223]:
# top 10 airports by number of flights
px.bar(x=top10_flights_passen.origin, y=top10_flights_passen.flights)

In [224]:
# top 10 airports by number of passengers
px.bar(x=top10_flights_passen.origin, y=top10_flights_passen.passengers)

# **Task 10**: Do bigger delays lead to bigger fuel comsumption per passenger? 
We need to do four things to answer this as accurate as possible:
- Find out average monthly delay per air carrier (monthly delay is sum of all delays in 1 month)
- Find out distance covered monthly by different air carriers
- Find out number of passengers that were carried by different air carriers
- Find out total fuel comsumption per air carrier.

Use this information to get the average fuel comsumption per passenger per km. Is this higher for the airlines with bigger average delays?

## Top carriers

In [225]:
px.bar(flights.mkt_carrier.value_counts())

In [ ]:
# top 4 carriers
big_carriers = flights.mkt_carrier.value_counts()[:4].index.tolist()
big_carriers

['AA', 'DL', 'UA', 'WN']

## Slow Carriers:

In [ ]:
slow_carriers = flights[['mkt_carrier', 'carrier_delay']].fillna(value={'carrier_delay' : 0})
slow_carriers = slow_carriers.groupby('mkt_carrier').sum().sort_values('carrier_delay', ascending=False)
slow_carriers['delay_%_of_total'] = slow_carriers.carrier_delay / slow_carriers.carrier_delay.sum()
slow_carriers = slow_carriers.reset_index()
slow_carriers

mkt_carrier  carrier_delay  delay_%_of_total
0           AA        53999.0          0.258670
1           UA        52138.0          0.249756
2           DL        41199.0          0.197355
3           WN        28551.0          0.136767
4           B6        13674.0          0.065502
5           G4         6422.0          0.030763
6           AS         5601.0          0.026830
7           F9         3604.0          0.017264
8           NK         2123.0          0.010170
9           HA         1399.0          0.006702
10          VX           46.0          0.000220

In [ ]:
carriers = flights.mkt_carrier.value_counts().to_frame().reset_index()
carriers['flights_%_of_total'] = carriers.mkt_carrier / carriers.mkt_carrier.sum()
carriers = carriers.rename(columns={'index': 'mkt_carrier', 'mkt_carrier' : 'carrier_flights'})
carriers = carriers.astype({'mkt_carrier' : 'object'})
carriers


mkt_carrier  carrier_flights  flights_%_of_total
0           AA            13006             0.26012
1           DL            10845             0.21690
2           UA             9692             0.19384
3           WN             8701             0.17402
4           AS             2629             0.05258
5           B6             1918             0.03836
6           NK             1193             0.02386
7           F9              798             0.01596
8           G4              608             0.01216
9           HA              554             0.01108
10          VX               56             0.00112

In [ ]:
carriers_flights_delays = pd.merge(carriers, slow_carriers, on='mkt_carrier', how='left')
carriers_flights_delays['exess_delay'] = carriers_flights_delays['delay_%_of_total'] - carriers_flights_delays['flights_%_of_total']
carriers_flights_delays

mkt_carrier  carrier_flights  flights_%_of_total  carrier_delay  \
0           AA            13006             0.26012        53999.0   
1           DL            10845             0.21690        41199.0   
2           UA             9692             0.19384        52138.0   
3           WN             8701             0.17402        28551.0   
4           AS             2629             0.05258         5601.0   
5           B6             1918             0.03836        13674.0   
6           NK             1193             0.02386         2123.0   
7           F9              798             0.01596         3604.0   
8           G4              608             0.01216         6422.0   
9           HA              554             0.01108         1399.0   
10          VX               56             0.00112           46.0   

    delay_%_of_total  exess_delay  
0           0.258670    -0.001450  
1           0.197355    -0.019545  
2           0.249756     0.055916  
3           0.136767    -0.037253  
4           0.026830    -0.025750  
5           0.065502     0.027142  
6           0.010170    -0.013690  
7           0.017264     0.001304  
8           0.030763     0.018603  
9           0.006702    -0.004378  
10          0.000220    -0.000900

In [ ]:
px.bar(carriers_flights_delays.drop(['mkt_carrier', 'carrier_flights', 'carrier_delay', 'exess_delay'], axis=1),
    barmode='group')

In [ ]:
px.bar(carriers_flights_delays[['mkt_carrier', 'exess_delay']].sort_values('exess_delay').set_index('mkt_carrier'))

In [250]:
carriers_flights_delays[['mkt_carrier', 'exess_delay']].set_index('mkt_carrier').exess_delay.to_dict()

{'AA': -0.001449590526739375,
 'DL': -0.01954519343156605,
 'UA': 0.05591569564467608,
 'WN': -0.03725267355189793,
 'AS': -0.025749633447661385,
 'B6': 0.027142308915671882,
 'NK': -0.013690232424457261,
 'F9': 0.0013041744428902644,
 'G4': 0.018603187644906014,
 'HA': -0.00437839621376152,
 'VX': -0.000899647052060779}

# By airport size

In [319]:
# top 10 airports by # of flights
airports = flights.copy()[['origin', 'origin_airport_id']]
airports = airports.groupby('origin').count().sort_values('origin_airport_id', ascending=False).reset_index()
airports

origin  origin_airport_id
0      ORD               2488
1      ATL               2452
2      DFW               1799
3      DEN               1720
4      CLT               1609
..     ...                ...
360    BET                  1
361    GST                  1
362    ADQ                  1
363    OGD                  1
364    APN                  1

[365 rows x 2 columns]

In [320]:
# top 10 airports by number of passengers
passengers_airp = pd.read_csv('C:/Users/danfv/OneDrive/Knowledge/Courses/Data Analysis/LHL - Data Analysis Bootcamp/lighthouse-data-notes/W6 Midterm Project/Midterm_Project/Data/Passengers - Aiports Count.csv')
passengers_airp

origin  count
0       ORD  78217
1       ATL  65253
2       DEN  57153
3       LAX  52241
4       IAH  46173
...     ...    ...
2510    CEL      1
2511    SC6      1
2512    LA3      1
2513    CEV      1
2514    LA1      1

[2515 rows x 2 columns]

In [321]:
# airports by number of flights AND passengers
flights_passen = pd.merge(airports, passengers_airp, on='origin', how='left')
flights_passen = flights_passen.rename(columns={'origin_airport_id' : 'flights', 'count' : 'passengers'})
flights_passen

origin  flights  passengers
0      ORD     2488       78217
1      ATL     2452       65253
2      DFW     1799       43244
3      DEN     1720       57153
4      CLT     1609       35573
..     ...      ...         ...
360    BET        1       21365
361    GST        1        1032
362    ADQ        1        3260
363    OGD        1         170
364    APN        1         189

[365 rows x 3 columns]

In [322]:
# top 10 airports by number of flights
px.bar(x=flights_passen.origin, y=flights_passen.flights)

In [332]:
# top 10 airports by number of passengers
px.bar(x=flights_passen.origin, y=flights_passen.passengers)

In [327]:
flights_passen['flights_%'] = flights_passen.flights / flights_passen.flights.sum()
flights_passen['passengers_%'] = flights_passen.passengers / flights_passen.passengers.sum()
flights_passen

origin  flights  passengers  flights_%  passengers_%
0      ORD     2488       78217    0.04976      0.042113
1      ATL     2452       65253    0.04904      0.035133
2      DFW     1799       43244    0.03598      0.023283
3      DEN     1720       57153    0.03440      0.030772
4      CLT     1609       35573    0.03218      0.019153
..     ...      ...         ...        ...           ...
360    BET        1       21365    0.00002      0.011503
361    GST        1        1032    0.00002      0.000556
362    ADQ        1        3260    0.00002      0.001755
363    OGD        1         170    0.00002      0.000092
364    APN        1         189    0.00002      0.000102

[365 rows x 5 columns]

In [328]:
flights_passen[['origin', 'flights_%']].set_index('origin')['flights_%'].to_dict()

{'ORD': 0.04976,
 'ATL': 0.04904,
 'DFW': 0.03598,
 'DEN': 0.0344,
 'CLT': 0.03218,
 'LAX': 0.03138,
 'SEA': 0.024,
 'DTW': 0.02234,
 'IAH': 0.02232,
 'PHX': 0.0222,
 'SFO': 0.02218,
 'LAS': 0.02098,
 'LGA': 0.0205,
 'EWR': 0.02008,
 'MSP': 0.01992,
 'PHL': 0.01914,
 'BOS': 0.01854,
 'DCA': 0.01814,
 'MCO': 0.01688,
 'JFK': 0.0166,
 'SLC': 0.01512,
 'BWI': 0.01352,
 'FLL': 0.01284,
 'SAN': 0.01276,
 'IAD': 0.01252,
 'MDW': 0.01122,
 'MIA': 0.01078,
 'BNA': 0.01044,
 'PDX': 0.01022,
 'TPA': 0.0099,
 'SJC': 0.00898,
 'STL': 0.00896,
 'DAL': 0.0089,
 'RDU': 0.00842,
 'AUS': 0.00808,
 'HOU': 0.00716,
 'MSY': 0.007,
 'HNL': 0.00698,
 'IND': 0.00696,
 'SMF': 0.00682,
 'CLE': 0.00676,
 'OAK': 0.00674,
 'PIT': 0.00656,
 'CMH': 0.00632,
 'CVG': 0.00628,
 'MCI': 0.00626,
 'SNA': 0.00528,
 'SAT': 0.00524,
 'MKE': 0.0048,
 'JAX': 0.00444,
 'RSW': 0.00422,
 'BUR': 0.00398,
 'BDL': 0.0039,
 'BUF': 0.0039,
 'SDF': 0.00366,
 'OMA': 0.00364,
 'PBI': 0.00364,
 'SJU': 0.00346,
 'ORF': 0.00346,
 'ABQ': 0.

In [329]:
flights_passen[['origin', 'passengers_%']].set_index('origin')['passengers_%'].to_dict()

{'ORD': 0.04211271586825138,
 'ATL': 0.035132785053773576,
 'DFW': 0.023282947249404384,
 'DEN': 0.030771674316557415,
 'CLT': 0.019152813858640788,
 'LAX': 0.028127010620112258,
 'SEA': 0.017266229658245057,
 'DTW': 0.023651218822769306,
 'IAH': 0.024859946428331066,
 'PHX': 0.01658568101974614,
 'SFO': 0.01793654853081717,
 'LAS': 0.015935283270294646,
 'LGA': 0.011639858398503223,
 'EWR': 0.022154442545058082,
 'MSP': 0.023263026126283767,
 'PHL': 0.01716716245137496,
 'BOS': 0.014261908928162814,
 'DCA': 0.010507046424293003,
 'MCO': 0.01624594510922967,
 'JFK': 0.0201924811220438,
 'SLC': 0.013807491957519551,
 'BWI': 0.010323987455076521,
 'FLL': 0.013969014577416446,
 'SAN': 0.008028212617608657,
 'IAD': 0.014227989177984467,
 'MDW': 0.006434522767959297,
 'MIA': 0.02304389377195698,
 'BNA': 0.00836041080586327,
 'PDX': 0.009484608240345659,
 'TPA': 0.009368311954019895,
 'SJC': 0.00536955029410577,
 'STL': 0.00816281480085607,
 'DAL': 0.005142880217517128,
 'RDU': 0.00798298628